In [1]:
import json
import nltk

In [45]:
with open('gg2020.json', encoding='utf8') as json_file:
    data = [json.loads(line) for line in json_file]

In [46]:
import re
import string
from nltk.corpus import stopwords 
stop_words = set(stopwords.words('english')) 

In [47]:
import demoji
demoji.download_codes()

... OK (Got response in 0.21 seconds)
Writing emoji data to C:\Users\victo\.demoji/codes.json ...
... OK


In [48]:
def remove_punct(text):
    text  = "".join([char for char in text if char not in string.punctuation])
    text = re.sub('[0-9]+', '', text)
    return text

In [49]:
clean_data = []
count = 0
for tweet in data:
    tweet_text = tweet['text']
    no_http = re.sub('http://\S+|https://\S+', '', tweet_text)
    emoji_list = demoji.findall(no_http)
    tweet_token = nltk.word_tokenize(no_http)
    filtered_tweet = tweet_token
    #filtered_tweet = [w for w in tweet_token if not w in stop_words] 
    filtered_tweet = [w for w in filtered_tweet if not w in emoji_list]
    filtered_tweet = [w for w in filtered_tweet if not w in string.punctuation]
    filtered_tweet = [w for w in filtered_tweet if w.isalnum()]
    filtered_tweet = [w.lower() for w in filtered_tweet]
    clean_data.append(filtered_tweet)

TypeError: list indices must be integers or slices, not str

In [56]:
for i in range(10):
    print(clean_data[i])

['priyanka', 'chopra', 'and', 'nick', 'jonas', 'at', 'the', '77th', 'annual', 'golden', 'globe', 'awards', 'present', 'the', 'award', 'for', 'best', 'tv', 'series', 'for', 'a', 'musical', 'or', 'comedy', 'goldenglobes2020', 'golden', 'globes']
['salma', 'hayek', 'salmahayek', 'in', 'blue', 'top', 'and', 'white', 'skirt', 'during', 'attend', '21st', 'annual', 'warner', 'and', 'instyle', 'golden', 'globe', 'after', 'party', 'in', 'beverly', 'hills', 'salmahayek', 'goldenglobes', 'goldenglobes2020', 'beverlyhills', 'goldenglobesawards2020']
['love', 'it', 'golden', 'globes', 'read', 'ricky', 'gervais', 'scathing', 'opening', 'monologue', 'via', 'thr']
['go', 'ricky', 'g']
['jcolburnlevy', 'wears', 'stevenkhalil', 'dame', 'en', 'fleurs', 'collection', 'gown', 'at', 'to', 'the', '77th', 'annual', 'golden', 'globe', 'awards', 'styled', 'by', 'taraswennen', 'catch', 'her', 'in', 'zoeysplaylist', 'starting', 'january', '7th', 'on', 'nbc']
['rickygervais', 'golden', 'at', 'the', 'golden', 'glob

In [50]:
print(data[0])

{'_id': {'$oid': '5e17fa7e174f9084edc115f2'}, 'user_id': '2414944424', 'text': '• Priyanka Chopra and Nick Jonas at the 77th Annual Golden Globe Awards present the award for Best TV series for a musical or comedy • #goldenglobes2020 @ Golden Globes https://t.co/fivnKsE9Ib', 'created_at': '2020-01-06T23:59:57', 'user': 'COttavianoNYC', 'id': '1214335827507122176'}


In [22]:
# search host
host_list = ['host', 'hosts', 'hosting', 'hosted']
host_tweet = []
for tweet in clean_data:
    for test_word in host_list:
        if test_word in tweet:
            host_tweet.append(tweet)
            break

In [73]:
print(len(host_tweet))

4882


In [75]:
from nltk.chunk import conlltags2tree, tree2conlltags

In [82]:
tag = nltk.pos_tag(clean_data[0])
pattern = 'NP: {<DT>?<JJ>*<NN>}'
cp = nltk.RegexpParser(pattern)
cs = cp.parse(tag)
iob = tree2conlltags(cs)
print(iob)

[('priyanka', 'NN', 'B-NP'), ('chopra', 'NN', 'B-NP'), ('and', 'CC', 'O'), ('nick', 'JJ', 'B-NP'), ('jonas', 'NN', 'I-NP'), ('at', 'IN', 'O'), ('the', 'DT', 'O'), ('77th', 'CD', 'O'), ('annual', 'JJ', 'B-NP'), ('golden', 'JJ', 'I-NP'), ('globe', 'NN', 'I-NP'), ('awards', 'NNS', 'O'), ('present', 'VBD', 'O'), ('the', 'DT', 'B-NP'), ('award', 'NN', 'I-NP'), ('for', 'IN', 'O'), ('best', 'JJS', 'O'), ('tv', 'NN', 'B-NP'), ('series', 'NN', 'B-NP'), ('for', 'IN', 'O'), ('a', 'DT', 'O'), ('musical', 'JJ', 'O'), ('or', 'CC', 'O'), ('comedy', 'NN', 'B-NP'), ('goldenglobes2020', 'NNS', 'O'), ('golden', 'JJ', 'O'), ('globes', 'NNS', 'O')]


In [7]:
import spacy

In [23]:
i = 0
nlp = spacy.load("en_core_web_sm")
doc = nlp(' '.join(word for word in clean_data[i]))
print(' '.join(word for word in clean_data[i]))
for ent in doc.ents:
    print(ent.text, ent.start_char, ent.end_char, ent.label_)

priyanka chopra and nick jonas at the 77th annual golden globe awards present the award for best tv series for a musical or comedy goldenglobes2020 golden globes
priyanka chopra 0 15 PERSON
nick jonas 20 30 PERSON
77th 38 42 ORDINAL
annual golden globe 43 62 EVENT
goldenglobes2020 golden globes 131 161 PERSON


In [30]:
name_list = []
for tweet in host_tweet:
    doc = nlp(' '.join(word for word in tweet))
    for ent in doc.ents:
        if ent.label_ == "PERSON":
            name_list.append(ent.text)

In [31]:
unique_list = list(set(name_list))

In [33]:
print(unique_list)

['rickygervais joaquinphoenix goldenglobes', 'tiffany haddish', 'gervais kicks', 'tim', 'katy perry', 'brad pitt ellen', 'george clooney', 'etnow hanks', 'elton john', 'ricky gervais w', 'wait rickey gervais', 'eddie griffin', 'horrible goldenglobes2020', 'tim allen dakota', 'ricky gervais returns', 'genesiselijah harlo786 rickygervais tim cook', 'rick gervais', 'patricia arquette', 'rickygervais golden globes', 'rickygervais awesome', 'joker doesn', 'joaquin', 'rickygervais exactly sycophants', 'john mulvaney', 'nyc', 'kim soohyun', 'laverne cox golden globes', 'steven wright', 'barry', 'goldenglobes host', 'yashar journogeoffz', 'jason momoa', 'lorenzo soria', 's golden globes', 'ricky gervais golden globes host', 'raymond arroyo golden globes', 'actors4makingleftypoliticalspeeches', 'ghislaine maxwell', 'gervais guy', 'jane fonda', 'emmys', 'kyle rudolph', 'eddietrunk fyi jimmy kimmel', 'robert pattinson', 'ditz head', 'rickygervais dude', 'amazon apple tcot kag', 'kevin frasier', '

In [34]:
counter = []
for item in unique_list:
    counter.append(name_list.count(item))

In [35]:
print(counter)

[1, 5, 9, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 13, 2, 3, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 13, 1, 2, 1, 1, 13, 16, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 2, 9, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 11, 1, 1, 1, 25, 1, 1, 1, 7, 1, 1, 1, 8, 1, 1, 1, 1, 1, 35, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 7, 1, 1, 2, 1, 2, 1, 4, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 5, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 3, 1, 1, 1, 7, 1, 1, 1, 1, 2, 1, 1, 1, 3, 2, 1, 1, 1, 1, 1, 1, 2, 1, 16, 1, 1, 1, 3, 1, 1, 1, 1, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 4, 1, 1, 18, 1, 1, 1, 1, 1, 1, 13, 1, 1, 1, 1, 1, 1, 1, 1, 2, 3, 4, 1, 1, 1, 1, 1, 1, 6, 1, 1, 1, 1, 1, 4, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 2, 3, 1, 1, 1, 1, 1, 2, 1, 2, 4, 1, 1, 1, 2, 1, 1, 11, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 6, 1, 2, 2, 1, 1, 1

In [37]:
name = unique_list[counter.index(max(counter))]

In [38]:
print(name)

ricky gervais


In [44]:
print(unique_list[counter.index(602)])

amazon apple


In [42]:
for tweet in data:
    print(tweet['created_at'])

2020-01-06T23:59:57
2020-01-06T23:59:54
2020-01-06T23:59:54
2020-01-06T23:59:53
2020-01-06T23:59:53
2020-01-06T23:59:51
2020-01-06T23:59:51
2020-01-06T23:59:51
2020-01-06T23:59:50
2020-01-06T23:59:49
2020-01-06T23:59:49
2020-01-06T23:59:49
2020-01-06T23:59:48
2020-01-06T23:59:47
2020-01-06T23:59:47
2020-01-06T23:59:43
2020-01-06T23:59:42
2020-01-06T23:59:40
2020-01-06T23:59:36
2020-01-06T23:59:33
2020-01-06T23:59:33
2020-01-06T23:59:33
2020-01-06T23:59:32
2020-01-06T23:59:30
2020-01-06T23:59:29
2020-01-06T23:59:29
2020-01-06T23:59:29
2020-01-06T23:59:24
2020-01-06T23:59:18
2020-01-06T23:59:16
2020-01-06T23:59:14
2020-01-06T23:59:13
2020-01-06T23:59:13
2020-01-06T23:59:11
2020-01-06T23:59:09
2020-01-06T23:59:07
2020-01-06T23:59:07
2020-01-06T23:59:02
2020-01-06T23:58:53
2020-01-06T23:58:52
2020-01-06T23:58:49
2020-01-06T23:58:49
2020-01-06T23:58:46
2020-01-06T23:58:43
2020-01-06T23:58:42
2020-01-06T23:58:41
2020-01-06T23:58:41
2020-01-06T23:58:40
2020-01-06T23:58:39
2020-01-06T23:58:37


2020-01-06T22:53:45
2020-01-06T22:53:44
2020-01-06T22:53:44
2020-01-06T22:53:42
2020-01-06T22:53:42
2020-01-06T22:53:40
2020-01-06T22:53:39
2020-01-06T22:53:37
2020-01-06T22:53:34
2020-01-06T22:53:33
2020-01-06T22:53:32
2020-01-06T22:53:28
2020-01-06T22:53:26
2020-01-06T22:53:25
2020-01-06T22:53:24
2020-01-06T22:53:14
2020-01-06T22:53:13
2020-01-06T22:53:13
2020-01-06T22:53:12
2020-01-06T22:53:04
2020-01-06T22:53:04
2020-01-06T22:53:02
2020-01-06T22:52:59
2020-01-06T22:52:58
2020-01-06T22:52:52
2020-01-06T22:52:51
2020-01-06T22:52:50
2020-01-06T22:52:48
2020-01-06T22:52:47
2020-01-06T22:52:46
2020-01-06T22:52:46
2020-01-06T22:52:43
2020-01-06T22:52:43
2020-01-06T22:52:41
2020-01-06T22:52:40
2020-01-06T22:52:39
2020-01-06T22:52:37
2020-01-06T22:52:36
2020-01-06T22:52:33
2020-01-06T22:52:32
2020-01-06T22:52:29
2020-01-06T22:52:29
2020-01-06T22:52:29
2020-01-06T22:52:28
2020-01-06T22:52:27
2020-01-06T22:52:26
2020-01-06T22:52:22
2020-01-06T22:52:20
2020-01-06T22:52:18
2020-01-06T22:52:15


2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T22:00:00
2020-01-06T21:59:59
2020-01-06T21:59:54
2020-01-06T21:59:54
2020-01-06T21:59:53
2020-01-06T21:59:51
2020-01-06T21:59:50
2020-01-06T21:59:49
2020-01-06T21:59:46
2020-01-06T21:59:46
2020-01-06T21:59:45
2020-01-06T21:59:45
2020-01-06T21:59:43
2020-01-06T21:59:41
2020-01-06T21:59:40
2020-01-06T21:59:39
2020-01-06T21:59:32
2020-01-06T21:59:31
2020-01-06T21:59:29
2020-01-06T21:59:28
2020-01-06T21:59:25
2020-01-06T21:59:24
2020-01-06T21:59:24
2020-01-06T21:59:23
2020-01-06T21:59:18
2020-01-06T21:59:16
2020-01-06T21:59:15
2020-01-06T21:59:14
2020-01-06T21:59:14
2020-01-06T21:59:10
2020-01-06T21:59:08
2020-01-06T21:59:07
2020-01-06T21:59:05
2020-01-06T21:59:04
2020-01-06T21:59:03
2020-01-06T21:59:03
2020-01-06T21:59:02
2020-01-06T21:59:01
2020-01-06T21:59:00
2020-01-06T21:59:00
2020-01-06T21:58:59


2020-01-06T21:11:36
2020-01-06T21:11:36
2020-01-06T21:11:36
2020-01-06T21:11:36
2020-01-06T21:11:35
2020-01-06T21:11:33
2020-01-06T21:11:32
2020-01-06T21:11:28
2020-01-06T21:11:26
2020-01-06T21:11:25
2020-01-06T21:11:23
2020-01-06T21:11:19
2020-01-06T21:11:18
2020-01-06T21:11:17
2020-01-06T21:11:14
2020-01-06T21:11:11
2020-01-06T21:11:11
2020-01-06T21:11:10
2020-01-06T21:11:07
2020-01-06T21:11:04
2020-01-06T21:10:59
2020-01-06T21:10:58
2020-01-06T21:10:58
2020-01-06T21:10:56
2020-01-06T21:10:56
2020-01-06T21:10:52
2020-01-06T21:10:51
2020-01-06T21:10:51
2020-01-06T21:10:50
2020-01-06T21:10:47
2020-01-06T21:10:42
2020-01-06T21:10:35
2020-01-06T21:10:34
2020-01-06T21:10:34
2020-01-06T21:10:33
2020-01-06T21:10:33
2020-01-06T21:10:33
2020-01-06T21:10:33
2020-01-06T21:10:32
2020-01-06T21:10:31
2020-01-06T21:10:30
2020-01-06T21:10:28
2020-01-06T21:10:27
2020-01-06T21:10:22
2020-01-06T21:10:20
2020-01-06T21:10:20
2020-01-06T21:10:18
2020-01-06T21:10:17
2020-01-06T21:10:14
2020-01-06T21:10:14


2020-01-06T20:25:37
2020-01-06T20:25:33
2020-01-06T20:25:32
2020-01-06T20:25:29
2020-01-06T20:25:27
2020-01-06T20:25:24
2020-01-06T20:25:21
2020-01-06T20:25:21
2020-01-06T20:25:15
2020-01-06T20:25:15
2020-01-06T20:25:15
2020-01-06T20:25:14
2020-01-06T20:25:13
2020-01-06T20:25:13
2020-01-06T20:25:12
2020-01-06T20:25:12
2020-01-06T20:25:11
2020-01-06T20:25:11
2020-01-06T20:25:08
2020-01-06T20:25:07
2020-01-06T20:25:05
2020-01-06T20:25:03
2020-01-06T20:25:02
2020-01-06T20:25:01
2020-01-06T20:24:58
2020-01-06T20:24:57
2020-01-06T20:24:57
2020-01-06T20:24:55
2020-01-06T20:24:54
2020-01-06T20:24:54
2020-01-06T20:24:52
2020-01-06T20:24:52
2020-01-06T20:24:50
2020-01-06T20:24:50
2020-01-06T20:24:49
2020-01-06T20:24:47
2020-01-06T20:24:44
2020-01-06T20:24:44
2020-01-06T20:24:44
2020-01-06T20:24:42
2020-01-06T20:24:42
2020-01-06T20:24:41
2020-01-06T20:24:38
2020-01-06T20:24:37
2020-01-06T20:24:37
2020-01-06T20:24:35
2020-01-06T20:24:34
2020-01-06T20:24:30
2020-01-06T20:24:29
2020-01-06T20:24:28


...

2020-01-05T08:11:43
2020-01-05T08:11:36
2020-01-05T08:11:34
2020-01-05T08:11:16
2020-01-05T08:11:16
2020-01-05T08:11:11
2020-01-05T08:11:10
2020-01-05T08:11:10
2020-01-05T08:11:06
2020-01-05T08:10:54
2020-01-05T08:10:18
2020-01-05T08:10:13
2020-01-05T08:10:12
2020-01-05T08:10:11
2020-01-05T08:10:09
2020-01-05T08:10:09
2020-01-05T08:09:47
2020-01-05T08:09:11
2020-01-05T08:08:26
2020-01-05T08:07:13
2020-01-05T08:06:26
2020-01-05T08:06:26
2020-01-05T08:06:26
2020-01-05T08:06:26
2020-01-05T08:06:26
2020-01-05T08:06:26
2020-01-05T08:06:22
2020-01-05T08:06:22
2020-01-05T08:05:46
2020-01-05T08:05:30
2020-01-05T08:05:23
2020-01-05T08:05:20
2020-01-05T08:04:58
2020-01-05T08:04:55
2020-01-05T08:04:35
2020-01-05T08:04:32
2020-01-05T08:04:32
2020-01-05T08:04:31
2020-01-05T08:04:31
2020-01-05T08:04:31
2020-01-05T08:04:30
2020-01-05T08:04:27
2020-01-05T08:04:22
2020-01-05T08:03:35
2020-01-05T08:03:04
2020-01-05T08:03:02
2020-01-05T08:02:39
2020-01-05T08:02:37
2020-01-05T08:02:37
2020-01-05T08:02:31


2020-01-04T23:24:43
2020-01-04T23:23:46
2020-01-04T23:23:38
2020-01-04T23:23:33
2020-01-04T23:23:33
2020-01-04T23:23:18
2020-01-04T23:23:07
2020-01-04T23:22:37
2020-01-04T23:22:36
2020-01-04T23:22:12
2020-01-04T23:22:06
2020-01-04T23:21:59
2020-01-04T23:21:57
2020-01-04T23:21:54
2020-01-04T23:21:45
2020-01-04T23:21:43
2020-01-04T23:21:35
2020-01-04T23:21:34
2020-01-04T23:21:33
2020-01-04T23:21:22
2020-01-04T23:21:21
2020-01-04T23:20:58
2020-01-04T23:20:40
2020-01-04T23:20:32
2020-01-04T23:20:28
2020-01-04T23:20:27
2020-01-04T23:20:23
2020-01-04T23:20:10
2020-01-04T23:20:04
2020-01-04T23:18:57
2020-01-04T23:18:18
2020-01-04T23:18:08
2020-01-04T23:18:02
2020-01-04T23:17:36
2020-01-04T23:17:24
2020-01-04T23:17:13
2020-01-04T23:17:12
2020-01-04T23:17:12
2020-01-04T23:17:07
2020-01-04T23:16:50
2020-01-04T23:16:45
2020-01-04T23:16:43
2020-01-04T23:16:39
2020-01-04T23:16:38
2020-01-04T23:16:28
2020-01-04T23:15:34
2020-01-04T23:15:14
2020-01-04T23:15:04
2020-01-04T23:14:58
2020-01-04T23:14:53


2020-01-04T14:24:03
2020-01-04T14:24:01
2020-01-04T14:23:54
2020-01-04T14:22:40
2020-01-04T14:22:08
2020-01-04T14:22:05
2020-01-04T14:21:28
2020-01-04T14:21:22
2020-01-04T14:20:43
2020-01-04T14:20:18
2020-01-04T14:19:27
2020-01-04T14:19:19
2020-01-04T14:18:13
2020-01-04T14:17:06
2020-01-04T14:17:00
2020-01-04T14:15:46
2020-01-04T14:15:14
2020-01-04T14:15:00
2020-01-04T14:14:19
2020-01-04T14:14:15
2020-01-04T14:14:08
2020-01-04T14:13:21
2020-01-04T14:12:30
2020-01-04T14:11:59
2020-01-04T14:11:54
2020-01-04T14:11:20
2020-01-04T14:10:59
2020-01-04T14:10:21
2020-01-04T14:08:21
2020-01-04T14:08:16
2020-01-04T14:08:06
2020-01-04T14:08:00
2020-01-04T14:05:45
2020-01-04T14:05:00
2020-01-04T14:03:47
2020-01-04T14:03:37
2020-01-04T14:03:24
2020-01-04T14:03:14
2020-01-04T14:03:05
2020-01-04T14:02:34
2020-01-04T14:02:29
2020-01-04T14:02:16
2020-01-04T14:02:15
2020-01-04T14:01:56
2020-01-04T14:01:43
2020-01-04T14:00:54
2020-01-04T14:00:48
2020-01-04T14:00:34
2020-01-04T14:00:21
2020-01-04T14:00:00


2020-01-03T22:59:56
2020-01-03T22:59:48
2020-01-03T22:59:43
2020-01-03T22:59:41
2020-01-03T22:59:31
2020-01-03T22:59:25
2020-01-03T22:59:19
2020-01-03T22:58:53
2020-01-03T22:58:38
2020-01-03T22:58:33
2020-01-03T22:57:37
2020-01-03T22:57:13
2020-01-03T22:56:55
2020-01-03T22:56:50
2020-01-03T22:56:40
2020-01-03T22:56:11
2020-01-03T22:56:04
2020-01-03T22:55:49
2020-01-03T22:55:18
2020-01-03T22:55:13
2020-01-03T22:55:08
2020-01-03T22:54:52
2020-01-03T22:54:32
2020-01-03T22:54:22
2020-01-03T22:54:05
2020-01-03T22:54:03
2020-01-03T22:53:50
2020-01-03T22:53:43
2020-01-03T22:53:29
2020-01-03T22:53:02
2020-01-03T22:52:56
2020-01-03T22:52:40
2020-01-03T22:52:01
2020-01-03T22:51:58
2020-01-03T22:51:56
2020-01-03T22:51:00
2020-01-03T22:50:52
2020-01-03T22:50:40
2020-01-03T22:50:36
2020-01-03T22:50:21
2020-01-03T22:50:12
2020-01-03T22:49:53
2020-01-03T22:49:45
2020-01-03T22:49:40
2020-01-03T22:49:07
2020-01-03T22:48:54
2020-01-03T22:48:43
2020-01-03T22:48:40
2020-01-03T22:48:29
2020-01-03T22:48:09


2020-01-03T14:12:47
2020-01-03T14:12:32
2020-01-03T14:10:52
2020-01-03T14:10:00
2020-01-03T14:09:25
2020-01-03T14:08:02
2020-01-03T14:06:47
2020-01-03T14:05:57
2020-01-03T14:05:19
2020-01-03T14:05:00
2020-01-03T14:04:58
2020-01-03T14:04:05
2020-01-03T14:03:56
2020-01-03T14:03:34
2020-01-03T14:03:34
2020-01-03T14:02:49
2020-01-03T14:02:32
2020-01-03T14:02:27
2020-01-03T14:02:25
2020-01-03T14:01:30
2020-01-03T14:00:39
2020-01-03T14:00:34
2020-01-03T14:00:23
2020-01-03T14:00:09
2020-01-03T13:59:34
2020-01-03T13:58:52
2020-01-03T13:57:13
2020-01-03T13:56:00
2020-01-03T13:55:47
2020-01-03T13:55:26
2020-01-03T13:54:51
2020-01-03T13:54:50
2020-01-03T13:54:43
2020-01-03T13:53:36
2020-01-03T13:53:20
2020-01-03T13:53:06
2020-01-03T13:52:20
2020-01-03T13:52:01
2020-01-03T13:52:00
2020-01-03T13:49:43
2020-01-03T13:48:40
2020-01-03T13:47:41
2020-01-03T13:46:32
2020-01-03T13:45:06
2020-01-03T13:44:20
2020-01-03T13:42:53
2020-01-03T13:42:51
2020-01-03T13:41:20
2020-01-03T13:39:50
2020-01-03T13:39:04
